# Real Estate Analysis - Valencia

## Import packages and libraries

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
import shapely
import json
import geopandas as gpd
import numpy as np

## Load the data

### Metro Stations

In [3]:
valencia_metro = pd.read_csv('./data/valencia_metro.csv')
valencia_metro = gpd.GeoDataFrame(valencia_metro,geometry=gpd.points_from_xy(valencia_metro.LONGITUDE, valencia_metro.LATITUDE),crs="EPSG:4326")
valencia_metro.head(5)

LONGITUDE   LATITUDE                   geometry
0  -0.402617  39.451070  POINT (-0.40262 39.45107)
1  -0.302844  39.620450  POINT (-0.30284 39.62045)
2  -0.311883  39.588189  POINT (-0.31188 39.58819)
3  -0.318336  39.555680  POINT (-0.31834 39.55568)
4  -0.320642  39.543297   POINT (-0.32064 39.5433)

### Neighborhoods

In [4]:
valencia_polygons = pd.read_csv('./data/valencia_polygons.csv')
valencia_polygons['GEO_SHAPE'] = valencia_polygons['GEO_SHAPE'].apply(shapely.wkt.loads)
valencia_polygons = gpd.GeoDataFrame(valencia_polygons, geometry='GEO_SHAPE', crs="EPSG:4326")
valencia_polygons.head(5)

NEIGHBORHOOD                                          GEO_SHAPE  \
0         La Seu  MULTIPOLYGON (((-0.37361 39.4805, -0.37404 39....   
1  Sant Francesc  MULTIPOLYGON (((-0.37974 39.47199, -0.37971 39...   
2     Jaume Roig  MULTIPOLYGON (((-0.36636 39.47941, -0.36592 39...   
3     La Roqueta  MULTIPOLYGON (((-0.38418 39.46927, -0.38404 39...   
4   Les Tendetes  MULTIPOLYGON (((-0.38268 39.4823, -0.38198 39....   

   REAL_ESTATE_TOTAL  UNITPRICE_MEAN     PRICE_MEAN  AGE_MEAN  QUALITY_MEAN  
0                250         2764.64  324652.000000      73.0          4.76  
1                833         3033.89  496545.018007      67.0          3.14  
2                234         2410.74  470508.547009      52.0          3.44  
3                389         2140.97  262383.033419      73.0          4.97  
4                151         1271.15  106721.854305      59.0          6.44

### Properties

In [5]:
valencia_sale = pd.read_csv('./data/valencia_sale.csv')
valencia_sale = gpd.GeoDataFrame(valencia_sale,geometry=gpd.points_from_xy(valencia_sale.LONGITUDE, valencia_sale.LATITUDE),crs="EPSG:4326")
valencia_sale.head(5)

PERIOD   PRICE    UNITPRICE  CONSTRUCTEDAREA  ROOMNUMBER  BATHNUMBER  \
0  201812  111000  1480.000000               75           2           1   
1  201812  169000  1320.312500              128           4           2   
2  201812  162000  1883.720930               86           2           1   
3  201812  199000  1792.792793              111           4           2   
4  201812   73000  1303.571429               56           3           1   

   HASTERRACE  HASLIFT  HASAIRCONDITIONING  AMENITYID  ...  \
0           1        1                   1          2  ...   
1           0        1                   1          3  ...   
2           0        1                   1          3  ...   
3           0        1                   0          3  ...   
4           1        1                   0          3  ...   

   DISTANCE_TO_CITY_CENTER  DISTANCE_TO_METRO  DISTANCE_TO_BLASCO  LONGITUDE  \
0                 3.759093           0.756517            3.373132  -0.393538   
1                 2.073773           0.370680            0.540594  -0.359125   
2                 2.099641           0.038560            0.719203  -0.362470   
3                 2.120917           0.524827            0.915379  -0.367417   
4                 3.087950           1.129985            2.009535  -0.370182   

    LATITUDE  AGE  TRIMESTER                   geometry  \
0  39.500908   23         T4  POINT (-0.39354 39.50091)   
1  39.482599   48         T4   POINT (-0.35912 39.4826)   
2  39.485144   14         T4  POINT (-0.36247 39.48514)   
3  39.487445   47         T4  POINT (-0.36742 39.48745)   
4  39.497057   64         T4  POINT (-0.37018 39.49706)   

                     BUILDTYPE    NEIGHBORHOOD  
0  Segunda mano en buen estado  Ciutat Fallera  
1  Segunda mano en buen estado      Benimaclet  
2  Segunda mano en buen estado      Benimaclet  
3  Segunda mano en buen estado      Benimaclet  
4  Segunda mano en buen estado     Els Orriols  

[5 rows x 44 columns]

## Exploratory Data Analysis

### Location of Metro Stations

In [7]:
fig_metro = px.scatter_map(valencia_metro, 
                           lat = "LATITUDE", 
                           lon="LONGITUDE", 
                           zoom=11,
                           width=1920,
                           height=1080,
                           title='Location of Metro Stations')

fig_metro.show()

fig_metro.write_image('./graphs/metro_stations.png')

### Number of properties by Neighborhood

In [8]:
geojson_data = valencia_polygons.geometry.to_json()
geojson_obj = json.loads(geojson_data)

for idx, feature in enumerate(geojson_obj['features']):
    neighborhood_name = valencia_polygons.loc[idx, 'NEIGHBORHOOD']
    feature['id'] = neighborhood_name

In [10]:
total_houses_neighborhood_map = px.choropleth_mapbox(valencia_polygons,
                                    geojson=geojson_obj, 
                                    locations='NEIGHBORHOOD',
                                    color='REAL_ESTATE_TOTAL', 
                                    mapbox_style="carto-positron",
                                    opacity=0.6,
                                    zoom = 12,
                                    center = {"lat": 39.46, "lon": -0.37},
                                    hover_data='NEIGHBORHOOD',
                                    title="Number of Properties by Neighborhood",
                                    width=1920,
                                    height=1080,
                                    labels={'REAL_ESTATE_TOTAL':'Total properties','NEIGHBORHOOD':'Neighborhood'})

total_houses_neighborhood_map.show()

total_houses_neighborhood_map.write_image('./graphs/total_houses_neighborhood_map.png')

### Average price per square meter by neighborhood

In [11]:
mean_m2price_neighborhood_map = px.choropleth_mapbox(valencia_polygons,
                                    geojson=geojson_obj, 
                                    locations='NEIGHBORHOOD',
                                    color='UNITPRICE_MEAN', 
                                    mapbox_style="carto-positron",
                                    opacity=0.6,
                                    zoom = 12,
                                    center = {"lat": 39.46, "lon": -0.37},
                                    hover_data='NEIGHBORHOOD',
                                    title="Average price per square meter by neighborhood",
                                    width=1920,
                                    height=1080,
                                    labels={'NEIGHBORHOOD':'Neighborhood','UNITPRICE_MEAN':'Average price per m² (€)'})

mean_m2price_neighborhood_map.show()

mean_m2price_neighborhood_map.write_image('./graphs/mean_m2price_neighborhood_map.png')

### Average age of properties by neighborhood

In [12]:
mean_age_per_neighborhood = px.choropleth_mapbox(valencia_polygons,
                                geojson=geojson_obj, 
                                locations='NEIGHBORHOOD',
                                color='AGE_MEAN', 
                                mapbox_style="carto-positron",
                                opacity=0.6,
                                zoom = 12,
                                center = {"lat": 39.46, "lon": -0.37},
                                hover_data='NEIGHBORHOOD',
                                title="Average age of properties by neighborhood",
                                width=1920,
                                height=1080,
                                labels={'AGE_MEAN':'Average age (years)','NEIGHBORHOOD':'Neighborhood'})

mean_age_per_neighborhood.show()

mean_age_per_neighborhood.write_image('./graphs/mean_age_per_neighborhood.png')

### Average quality according to the cadastre by neighborhood

In [14]:
quality_mean_neighborhood = px.choropleth_mapbox(valencia_polygons,
                                geojson=geojson_obj, 
                                locations='NEIGHBORHOOD',
                                color='QUALITY_MEAN', 
                                mapbox_style="carto-positron",
                                opacity=0.6,
                                zoom = 12,
                                center = {"lat": 39.46, "lon": -0.37},
                                hover_data='NEIGHBORHOOD',
                                title="Average quality according to the cadastre by neighborhood",
                                width=1920,
                                height=1080,
                                labels={'NEIGHBORHOOD':'Neighborhood','QUALITY_MEAN':'Average quality'})

quality_mean_neighborhood.update_coloraxes(
        colorscale="plasma",
        colorbar=dict(
            title=dict(text="", side="right", font=dict(size=16, weight=600)),
        ),
    )

quality_mean_neighborhood.show()

quality_mean_neighborhood.write_image('./graphs/quality_mean_neighborhood.png')

### Average type of construction by neighborhood

In [16]:
valencia_sale["BUILDTYPE"].unique()

array(['Segunda mano en buen estado', 'Segunda mano a reformar',
       'Nueva construcción'], dtype=object)

In [17]:
valencia_sale["BUILDTYPE"] = valencia_sale["BUILDTYPE"].replace({
    "Segunda mano en buen estado": "Second-hand Apartment in Good Condition",
    "Segunda mano a reformar": "Second-hand House to Renovate",
    "Nueva construcción": "New Construction"
})


scatter_map_buildtype = px.scatter_map(
                            data_frame=valencia_sale,
                            lat='LATITUDE',
                            lon='LONGITUDE',
                            zoom=12.5,
                            width=1920,
                            height=1080,
                            color="BUILDTYPE",
                            title='Average type of construction by neighborhood'
                            )

scatter_map_buildtype.update_traces(marker=dict(size=5))

scatter_map_buildtype.show()

scatter_map_buildtype.write_image('./graphs/scatter_map_buildtype.png')

### Correlation matrix: Variables that influence price the most

In [18]:
corr = valencia_sale.select_dtypes(np.number).corr()

text_values = [
    [f"{value:.2f}" if abs(value) > 0.2 else "" for value in row]
    for row in corr.values
]

trace_corr_matrix = go.Heatmap(z=corr.values,
                         x = corr.index.values,
                         y = corr.columns.values,
                         text=text_values,
                         colorscale='Viridis')

corr_matrix = go.Figure()
corr_matrix.add_trace(trace_corr_matrix)
corr_matrix.update_layout(width = 1920, height = 1920, xaxis = dict(title = 'Variables'), yaxis = dict(title = 'Variables'))

corr_matrix.update_traces(
    text=text_values,
    texttemplate="%{text}",
    textfont=dict(size=13, color="white"),
)

corr_matrix.show()

corr_matrix.write_image('./graphs/corr_matrix.png')

In [19]:
variables_corr_price = ["PRICE", "UNITPRICE"]
filtered_corr = corr.loc[variables_corr_price]

text_values_price = [
    [f"{value:.2f}" if abs(value) > 0.2 else "" for value in row]
    for row in filtered_corr.values
]

trace_corr_matrix_price = go.Heatmap(
    z=filtered_corr.values,
    x=filtered_corr.columns,
    y=filtered_corr.index,
    colorscale="Viridis",
    text=text_values_price,
    hoverinfo="z",
)

corr_matrix_price = go.Figure()
corr_matrix_price.add_trace(trace_corr_matrix_price)

corr_matrix_price.update_traces(
    text=text_values_price,
    texttemplate="%{text}",
    textfont=dict(size=15, color="white"),
)

corr_matrix_price.update_layout(
    title="Correlations between total price and price per m² with the other variables",
    xaxis=dict(title="Variables"),
    yaxis=dict(title="Variables"),
    width=1920,
    height=500,
)

corr_matrix_price.show()

corr_matrix_price.write_image('./graphs/corr_matrix_price.png')

### Properties by neighborhood

In [20]:
ordered_neig_total = valencia_polygons.sort_values(by='REAL_ESTATE_TOTAL', ascending=True)
top5 = ordered_neig_total.nlargest(10,'REAL_ESTATE_TOTAL').sort_values(by='REAL_ESTATE_TOTAL',ascending=True)

houses_per_neighborhood = px.bar(
                                top5,
                                x = 'REAL_ESTATE_TOTAL',
                                y = 'NEIGHBORHOOD',
                                orientation='h',
                                title='Number of Properties by Neighborhood',)

houses_per_neighborhood.update_layout(yaxis = dict(title = 'Name of the neighborhood'), xaxis = dict(title = 'Number of properties'), width = 750, height = 500)

### Properties by number of rooms

In [21]:
counts_bedrooms = valencia_sale.groupby(['ROOMNUMBER']).size().reset_index(name='count')

houses_per_roomnumber = px.bar(
                            counts_bedrooms,
                            x = 'count',
                            y = 'ROOMNUMBER',
                            orientation='h',
                            title='Number of Properties by Number of Rooms',)

houses_per_roomnumber.update_layout(yaxis = dict(range = [0,8], title = 'Number of rooms'), xaxis = dict(range = [0, 17000], title = 'Number of properties'), width = 750, height = 500)

### Properties by property type

In [23]:
counts_buildtype = valencia_sale.groupby(['BUILDTYPE']).size().reset_index(name='count')

houses_per_roomnumber = px.bar(
                            counts_buildtype,
                            x = 'count',
                            y = 'BUILDTYPE',
                            orientation='h',
                            title='Number of Properties by Type of Property',)

houses_per_roomnumber.update_layout(yaxis = dict(title = 'Type of Property'), xaxis = dict(range = [0, 30000], title = 'Number of properties'), width = 750, height = 500)

### Properties by number of bathrooms

In [24]:
counts_baths = valencia_sale.groupby(['BATHNUMBER']).size().reset_index(name='count')

houses_per_roomnumber = px.bar(
                            counts_baths,
                            x = 'count',
                            y = 'BATHNUMBER',
                            orientation='h',
                            title='Number of Properties by Number of Bathrooms',)

houses_per_roomnumber.update_layout(yaxis = dict(range = [0,6], title = 'Number of Bathrooms'), xaxis = dict(range = [0, 17000], title = 'Number of Properties'), width = 750, height = 500)

### Properties by cadastre quality

In [ ]:
d1 = valencia_sale[valencia_sale['ROOMNUMBER'] != 81]

d1['size_inverted'] = d1['CADASTRALQUALITYID'].max() - d1['CADASTRALQUALITYID']

scatter_map_quality = px.scatter_map(
                            data_frame=d1,
                            lat='LATITUDE',
                            lon='LONGITUDE',
                            zoom=12.5,
                            width=1920,
                            height=1080,
                            size="size_inverted",
                            color="CADASTRALQUALITYID",
                            size_max=7,
                            title='Distribution of properties by cadastral quality'
                            )
scatter_map_quality.show()
scatter_map_quality.write_image('./graphs/scatter_map_quality.png')


c:\Users\borog\anaconda3\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Properties map with filters

In [28]:
scatter_map_wfilters = px.scatter_map(
                            data_frame=valencia_sale,
                            lat='LATITUDE',
                            lon='LONGITUDE',
                            zoom=12.5,
                            width=1920,
                            height=1080,
                            title='Distribution of properties with filters')

scatter_map_wfilters.update_traces(marker=dict(size=5, color = "orange"))

scatter_map_wfilters.show()